In [1]:
# import necessary libraries

import os
import time
import json
import requests
import logging
import concurrent.futures
from dotenv import load_dotenv
import tenacity # for retrying failed requests
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import ast
import openpyxl
import pycountry
import random

# 1- Web Scraping 

In [ ]:
# Load environment variables from .env file
load_dotenv()

API_KEY = os.getenv("API_KEY")  
if not API_KEY:
    raise ValueError("❌ API_KEY مش موجود في ملف .env")

OUT_DIR = "data"
os.makedirs(OUT_DIR, exist_ok=True)
OUT_FILE = os.path.join(OUT_DIR, "movies_all.ndjson")

logging.basicConfig(level=logging.INFO,
                    format="%(asctime)s - %(levelname)s - %(message)s")
logger = logging.getLogger(__name__)

In [ ]:
# Function to fetch data from TMDB API with retries and exponential backoff

def fetch(endpoint, params=None, retries=10, backoff=2):
    base_url = "https://api.themoviedb.org/3"
    params = params or {}
    params["api_key"] = API_KEY
    url = f"{base_url}{endpoint}"

    for i in range(retries):
        try:
            response = requests.get(url, params=params, timeout=60)
            response.raise_for_status()
            return response.json()
        except (requests.exceptions.ConnectionError,
                requests.exceptions.Timeout) as e:
            wait = backoff * (i + 1)
            logger.warning(f"⚠️ Network error: {e}. Retrying in {wait}s...")
            time.sleep(wait)
        except Exception as e:
            logger.error(f"❌ Fatal error: {e}")
            raise
    raise Exception("Failed after retries")

In [ ]:
# Function to generate date ranges (yearly or half-yearly)

# step can be "year" or "half"
def generate_date_ranges(start_year=1900, end_year=2025, step="year"):
    ranges = []
    for y in range(start_year, end_year + 1):
        if step == "year":
            start = f"{y}-01-01"
            end = f"{y}-12-31"
            ranges.append((start, end))
        elif step == "half":
            # First half
            ranges.append((f"{y}-01-01", f"{y}-06-30"))
            # Second half
            ranges.append((f"{y}-07-01", f"{y}-12-31"))
    return ranges

In [ ]:
# Function to generate quarter date ranges

def generate_quarter_ranges(start_year=1900, end_year=2025):
    quarters = [
        ("01-01", "03-31"),
        ("04-01", "06-30"),
        ("07-01", "09-30"),
        ("10-01", "12-31"),
    ]
    ranges = []
    for year in range(start_year, end_year + 1):
        for q_start, q_end in quarters:
            start = f"{year}-{q_start}"
            end = f"{year}-{q_end}"
            ranges.append((start, end))
    return ranges

In [ ]:
# Function to generate monthly date ranges

def generate_monthly_ranges(start_year=1900, end_year=2025):
    import calendar
    ranges = []
    for year in range(start_year, end_year + 1):
        for month in range(1, 13):
            start = f"{year}-{month:02d}-01"
            last_day = calendar.monthrange(year, month)[1] # Get last day of the month
            end = f"{year}-{month:02d}-{last_day}" 
            ranges.append((start, end))
    return ranges

In [ ]:
# Function to discover movies with pagination and optional date range filtering

def discover_movies(pages=5, date_range=None, sort_by="popularity.desc"):
    results = []
    params = {"sort_by": sort_by}

    if date_range:
        params["primary_release_date.gte"] = date_range[0]
        params["primary_release_date.lte"] = date_range[1]

    for p in range(1, pages + 1):
        logger.info(f"--- Discover page {p} --- (range={date_range})")
        params["page"] = p
        r = fetch("/discover/movie", params)
        results.extend(r.get("results", []))

        # stop early if last page
        if p >= r.get("total_pages", 1):
            break

        time.sleep(0.1)  # respect rate-limit
    return results

In [ ]:
# Function to process a single movie and append details to ndjson file
def process_movie(movie_id, out_file):
    try:
        data = fetch(f"/movie/{movie_id}",
                     {"append_to_response": "credits,reviews"}) # Fetch movie details with credits and reviews
        with open(out_file, "a", encoding="utf-8") as f:
            f.write(json.dumps(data, ensure_ascii=False) + "\n") # Append movie data to ndjson file
            
        return None
    except Exception as e:
        logger.error(f"Failed {movie_id}: {e}")
        return movie_id

In [ ]:
# Function to process list of IDs concurrently

def process_ids(movie_ids, out_file, workers=16): # number of concurrent workers to use 
    failed = []
    with concurrent.futures.ThreadPoolExecutor(max_workers=workers) as executor: # Use ThreadPoolExecutor for I/O bound tasks
        futures = [executor.submit(process_movie, mid, out_file) # Submit tasks to executor
                   for mid in movie_ids] 
        for fut in concurrent.futures.as_completed(futures): # Process completed futures
            res = fut.result()
            if res:
                failed.append(res)
    return failed

In [ ]:
# Function to load existing IDs from ndjson file to avoid duplicates
def load_existing_ids(out_file):
    existing_ids = set()
    if os.path.exists(out_file):
        with open(out_file, "r", encoding="utf-8") as f:
            for line in f:
                try:
                    data = json.loads(line)
                    if "id" in data:
                        existing_ids.add(data["id"])
                except json.JSONDecodeError:
                    continue
    return existing_ids

In [ ]:

# Main pipeline function  

def main(pages=500, workers=16):
    all_movies = []
    seen = load_existing_ids(OUT_FILE)

    logger.info(f"Resume mode: Found {len(seen)} movies already saved ✅")

    # Read values from .env
    step = os.getenv("DATE_STEP", "year")  # "year" or "half"
    start_year = int(os.getenv("START_YEAR", "1900"))
    end_year = int(os.getenv("END_YEAR", "2025"))

    # ranges = generate_date_ranges(start_year, end_year, step=step)
    # ranges = generate_quarter_ranges(start_year, end_year)
    ranges = generate_monthly_ranges(start_year, end_year)


    for start, end in ranges:
        logger.info(f"Fetching movies between {start} and {end}")
        movies = discover_movies(pages=pages, date_range=(start, end))
        ids = [m["id"] for m in movies if m["id"] not in seen]
        seen.update(ids)
        all_movies.extend(ids)
        logger.info(f"Collected {len(ids)} new movies for {start} → {end}")

        # Save all into one file
        failed_ids = process_ids(ids, OUT_FILE, workers)

        # Retry failed IDs
        if failed_ids:
            logger.info(f"Retrying {len(failed_ids)} failed movies...")
            retry_failed = process_ids(failed_ids, OUT_FILE, workers)
            if retry_failed:
                fail_file = os.path.join(OUT_DIR, "failed_ids.txt")
                with open(fail_file, "w") as f:
                    f.write("\n".join(map(str, retry_failed)))
                logger.info(
                    f"Still failed after retry. Saved {len(retry_failed)} IDs to {fail_file}")
            else:
                logger.info("All failed IDs succeeded on retry ✅")

    logger.info(f"Total new movies downloaded: {len(all_movies)}")
    logger.info(f"Final data saved in {OUT_FILE}")
    logger.info("Pipeline finished!")


if __name__ == "__main__":
    main()

2025-09-29 21:05:25,606 - INFO - Resume mode: Found 946605 movies already saved ✅
2025-09-29 21:05:25,609 - INFO - Fetching movies between 1900-01-01 and 1900-01-31
2025-09-29 21:05:25,609 - INFO - --- Discover page 1 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:26,076 - INFO - --- Discover page 2 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:26,499 - INFO - --- Discover page 3 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:26,935 - INFO - --- Discover page 4 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:27,367 - INFO - --- Discover page 5 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:27,807 - INFO - --- Discover page 6 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:28,247 - INFO - --- Discover page 7 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:28,680 - INFO - --- Discover page 8 --- (range=('1900-01-01', '1900-01-31'))
2025-09-29 21:05:29,112 - INFO - --- Discover page 9 --- (range=('1900-01-01', '190

In [3]:

input_file = r"D:\depi_project\data\raw\movies_all.ndjson"   # file Large JSON
output_file = r"D:\depi_project\data\raw\movies_all.csv"  # output CSV file

# write CSV in chunks
chunksize = 100000    
batch = []
count = 0

with open(input_file, "r", encoding="utf-8") as f, open(output_file, "w", encoding="utf-8", newline="") as out_csv:
    writer = None

    for line in f:
        try:
            record = json.loads(line.strip())  # convert line to dict
            batch.append(record)
        except json.JSONDecodeError:
            continue  # If a line is corrupted, skip it 

        if len(batch) >= chunksize:
            df = pd.DataFrame(batch)

            if writer is None:
                df.to_csv(out_csv, index=False, header=True)
                writer = True
            else:
                df.to_csv(out_csv, index=False, header=False)

            count += len(batch)
            print(f"✅ Processed {count:,} records...")
            batch = []

    # Write remaining records
    if batch:
        df = pd.DataFrame(batch)
        if writer is None:
            df.to_csv(out_csv, index=False, header=True)
        else:
            df.to_csv(out_csv, index=False, header=False)
        count += len(batch)

print(f"🎉 Finished! Total {count:,} records saved to {output_file}")

✅ Processed 100,000 records...
✅ Processed 200,000 records...
✅ Processed 300,000 records...
✅ Processed 400,000 records...
✅ Processed 500,000 records...
✅ Processed 600,000 records...
✅ Processed 700,000 records...
✅ Processed 800,000 records...
✅ Processed 900,000 records...
🎉 Finished! Total 946,899 records saved to D:\depi_project\data\raw\movies_all.csv


# 2 - Data Cleaning and Preprocessing 

In [2]:
df = pd.read_csv(r"D:\depi_project\data\raw\movies_all.csv")

In [3]:
df.isnull().sum()

adult                         0
backdrop_path            609864
belongs_to_collection    918213
budget                        0
genres                        0
homepage                 828890
id                            0
imdb_id                  356662
origin_country                0
original_language             0
original_title                4
overview                 132196
popularity                    0
poster_path              194193
production_companies          0
production_countries          0
release_date                435
revenue                       0
runtime                       0
spoken_languages              0
status                        0
tagline                  803424
title                         4
video                         0
vote_average                  0
vote_count                    0
credits                       0
reviews                       0
dtype: int64

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 946899 entries, 0 to 946898
Data columns (total 28 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   adult                  946899 non-null  bool   
 1   backdrop_path          337035 non-null  object 
 2   belongs_to_collection  28686 non-null   object 
 3   budget                 946899 non-null  int64  
 4   genres                 946899 non-null  object 
 5   homepage               118009 non-null  object 
 6   id                     946899 non-null  int64  
 7   imdb_id                590237 non-null  object 
 8   origin_country         946899 non-null  object 
 9   original_language      946899 non-null  object 
 10  original_title         946895 non-null  object 
 11  overview               814703 non-null  object 
 12  popularity             946899 non-null  float64
 13  poster_path            752706 non-null  object 
 14  production_companies   946899 non-nu

In [3]:
df.drop(columns=['belongs_to_collection', 'backdrop_path',  'homepage',  'original_title',
        'poster_path', 'spoken_languages', 'status', 'tagline', 'video', 'credits', 'imdb_id'], inplace=True)
df

adult  budget                                             genres  \
0       False       0                                                 []   
1       False       0                     [{'id': 35, 'name': 'Comedy'}]   
2       False       0                                                 []   
3       False       0                [{'id': 99, 'name': 'Documentary'}]   
4       False       0                [{'id': 99, 'name': 'Documentary'}]   
...       ...     ...                                                ...   
946894  False       0                                                 []   
946895  False     300  [{'id': 28, 'name': 'Action'}, {'id': 35, 'nam...   
946896  False   17000                     [{'id': 28, 'name': 'Action'}]   
946897  False       0  [{'id': 27, 'name': 'Horror'}, {'id': 53, 'nam...   
946898  False       0  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   

             id origin_country original_language  \
0        195554         ['US']                en   
1        105303         ['GB']                xx   
2        195553         ['US']                en   
3        195569         ['US']                en   
4        195542         ['US']                en   
...         ...            ...               ...   
946894  1554419         ['US']                en   
946895  1554303         ['IT']                it   
946896  1554304         ['IN']                ta   
946897  1355140         ['ID']                id   
946898  1554299         ['DO']                es   

                                                 overview  popularity  \
0       This building and machinery supplied the elect...      6.3707   
1       An early trick film where a car explodes and b...      3.4255   
2       This is the building in which so many of the p...      3.2375   
3       This picture shows the remains of one of the d...      5.1725   
4       At the first news of the disast by cyclone and...      4.0098   
...                                                   ...         ...   
946894  After Paola is matched with a handsome online ...      0.0000   
946895                                                NaN      0.0000   
946896  Francis' father raises his voice for an import...      0.0000   
946897  Sabdo and Intan lived happily despite their ma...      0.9564   
946898                                                NaN      0.0000   

                                     production_companies  \
0                                                      []   
1       [{'id': 24148, 'logo_path': None, 'name': 'Hep...   
2                                                      []   
3       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
4       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
...                                                   ...   
946894                                                 []   
946895  [{'id': 275779, 'logo_path': None, 'name': 'Fa...   
946896                                                 []   
946897  [{'id': 5344, 'logo_path': '/QDZf41MZk122e61pZ...   
946898  [{'id': 168180, 'logo_path': None, 'name': 'Ca...   

                                     production_countries release_date  \
0                                                      []   1900-05-21   
1        [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   1900-07-01   
2                                                      []   1900-09-21   
3       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21   
4       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21   
...                                                   ...          ...   
946894                                                 []          NaN   
946895            [{'iso_3166_1': 'IT', 'name': 'Italy'}]   2025-10-21   
946896                                                 []   2025-12-19   
946897        [{'iso_3166_1': 'ID', 'name': 'Indonesia'}]   2025-12-24   
946898  [{'iso_3166_1': 'DO', 'name': 'Dominic

In [32]:
df.shape

(946899, 17)

In [4]:
# code ll genres

df["genres"] = df["genres"].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)

df["genre_names"] = df["genres"].apply(lambda lst: [d["name"] for d in lst])

# Create a string version of genre_names for display
df["genre_names_str"] = df["genre_names"].apply(lambda x: ", ".join(x))

print(df[["genres", "genre_names_str"]].head(10))



df.drop(columns='genres', axis=1, inplace=True)

                                              genres  \
0                                                 []   
1                     [{'id': 35, 'name': 'Comedy'}]   
2                                                 []   
3                [{'id': 99, 'name': 'Documentary'}]   
4                [{'id': 99, 'name': 'Documentary'}]   
5  [{'id': 14, 'name': 'Fantasy'}, {'id': 35, 'na...   
6                                                 []   
7  [{'id': 14, 'name': 'Fantasy'}, {'id': 35, 'na...   
8  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
9                      [{'id': 18, 'name': 'Drama'}]   

              genre_names_str  
0                              
1                      Comedy  
2                              
3                 Documentary  
4                 Documentary  
5             Fantasy, Comedy  
6                              
7             Fantasy, Comedy  
8  Animation, Comedy, Fantasy  
9                       Drama  


In [5]:
df["genre_names_str"].apply(lambda x: tuple(
    x) if isinstance(x, list) else x).unique()

df["genre_names_str"].apply(lambda x: tuple(
    x) if isinstance(x, list) else x).value_counts()

genre_names_str
                                                              211686
Documentary                                                   151659
Drama                                                         117208
Comedy                                                         61315
Animation                                                      33800
                                                               ...  
Animation, Drama, Mystery, Adventure                               1
Horror, Action, Adventure, Drama, Science Fiction, Fantasy         1
Family, Action, Drama, Thriller, Comedy                            1
Animation, Documentary, History, Family                            1
Comedy, Action, Thriller, Mystery                                  1
Name: count, Length: 14477, dtype: int64

In [6]:

# افترض إن الداتا موجودة في df والعمود اسمه genre_names_str
values = ['Documentary', 'Drama', 'Comedy', 'Animation']


def fill_genre(x):
    if pd.isna(x) or x.strip() == '' or x.strip().lower() == 'unknown':
        return random.choice(values)
    return x


df['genre_names_str'] = df['genre_names_str'].apply(fill_genre)

In [7]:
def str_to_list(x):
    if pd.isna(x) or x.strip() == '' or x.strip().lower() == 'unknown':
        return []   # لو فاضي أو Unknown خليه ليست فاضية
    # نفصل القيم حسب الفاصلة ونشيل المسافات الزايدة
    return [genre.strip() for genre in x.split(',') if genre.strip() != '']


df['genre_names_list'] = df['genre_names_str'].apply(str_to_list)

In [60]:
df

adult  budget       id origin_country original_language  \
0       False       0   195554         ['US']                en   
1       False       0   105303         ['GB']                xx   
2       False       0   195553         ['US']                en   
3       False       0   195569         ['US']                en   
4       False       0   195542         ['US']                en   
...       ...     ...      ...            ...               ...   
946894  False       0  1554419         ['US']                en   
946895  False     300  1554303         ['IT']                it   
946896  False   17000  1554304         ['IN']                ta   
946897  False       0  1355140         ['ID']                id   
946898  False       0  1554299         ['DO']                es   

                                                 overview  popularity  \
0       This building and machinery supplied the elect...      6.3707   
1       An early trick film where a car explodes and b...      3.4255   
2       This is the building in which so many of the p...      3.2375   
3       This picture shows the remains of one of the d...      5.1725   
4       At the first news of the disast by cyclone and...      4.0098   
...                                                   ...         ...   
946894  After Paola is matched with a handsome online ...      0.0000   
946895                                                NaN      0.0000   
946896  Francis' father raises his voice for an import...      0.0000   
946897  Sabdo and Intan lived happily despite their ma...      0.9564   
946898                                                NaN      0.0000   

                                     production_companies  \
0                                                      []   
1       [{'id': 24148, 'logo_path': None, 'name': 'Hep...   
2                                                      []   
3       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
4       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
...                                                   ...   
946894                                                 []   
946895  [{'id': 275779, 'logo_path': None, 'name': 'Fa...   
946896                                                 []   
946897  [{'id': 5344, 'logo_path': '/QDZf41MZk122e61pZ...   
946898  [{'id': 168180, 'logo_path': None, 'name': 'Ca...   

                                     production_countries release_date  \
0                                                      []   1900-05-21   
1        [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   1900-07-01   
2                                                      []   1900-09-21   
3       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21   
4       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21   
...                                                   ...          ...   
946894                                                 []          NaN   
946895            [{'iso_3166_1': 'IT', 'name': 'Italy'}]   2025-10-21   
946896                                                 []   2025-12-19   
946897        [{'iso_3166_1': 'ID', 'name': 'Indonesia'}]   2025-12-24   
946898  [{'iso_3166_1': 'DO', 'name': 'Dominican Repub...   2025-12-04   

        revenue  runtime                                     title  \
0             0        1         Panorama of Galveston Power House   
1             0        2                  Explosion of a Motor Car   
2             0        1      Panorama of Orphans' Home, Galveston   
3             0        1       Panorama of Wreckage of Water Front   
4             0        1  Bird's-Eye View of Dock Front, Galveston   
...         ...      ...                                       ...   
946894        0        0                                     Match   
946895        0        0                     L'Impermeabile Giallo   
946896        0      100                        FRANCIS: Chapter-1   
9468

In [8]:
df['overview'] = df['overview'].fillna('No overview available')

# تحويل النص لـ dict
df["reviews"] = df["reviews"].apply(
    lambda x: ast.literal_eval(x) if isinstance(x, str) else x)

# استخراج عدد الريفيوهات
df["n_reviews"] = df["reviews"].apply(lambda d: d.get("total_results", 0))

# استخراج الريفيوهات لو فيه
df["review_texts"] = df["reviews"].apply(
    lambda d: [r.get("content", "") for r in d.get("results", [])])

In [9]:
df = df.dropna(subset=['release_date','title'])

In [19]:
df.isnull().sum()

adult                               0
budget                              0
id                                  0
origin_country                      0
original_language                   0
overview                            0
popularity                          0
production_companies                0
production_countries                0
release_date                        0
revenue                             0
runtime                             0
title                               0
vote_average                        0
vote_count                          0
genre_names                         0
genre_names_str                     0
genre_names_list                    0
production_company_names            0
production_company_countries        0
production_company_names_str        0
production_company_countries_str    0
release_year                        0
release_month                       0
release_day                         0
dtype: int64

In [10]:
df.drop(columns='reviews', axis=1, inplace=True)

C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\2225894870.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns='reviews', axis=1, inplace=True)


In [11]:
# عدد كل الصفوف (الأفلام)
total_movies = df["n_reviews"].count()

# عدد الأفلام اللي عندها ريفيوهات
movies_with_reviews = (df["n_reviews"] > 0).sum()

# عدد الأفلام اللي مالهاش ريفيوهات
movies_without_reviews = (df["n_reviews"] == 0).sum()
stats = {
    "Total movies": [total_movies],
    "Movies with reviews": [movies_with_reviews],
    "Movies without reviews": [movies_without_reviews]
}

print(pd.DataFrame(stats))

   Total movies  Movies with reviews  Movies without reviews
0        946460                21738                  924722


In [12]:
df['runtime'] = df['runtime'].astype('float64')
df.drop(columns=['n_reviews', 'review_texts'],axis=1,inplace=True )

C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\3922254613.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['runtime'] = df['runtime'].astype('float64')
C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\3922254613.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns=['n_reviews', 'review_texts'],axis=1,inplace=True )


In [13]:

df["production_companies"] = df["production_companies"].apply(
    lambda x: ast.literal_eval(x) if isinstance(x, str) else x
)

df["production_company_names"] = df["production_companies"].apply(
    lambda lst: [d.get("name", "Unknown")
                 for d in lst] if isinstance(lst, list) else []
)



def get_country_names(lst):
    if isinstance(lst, list):
        countries = []
        for d in lst:
            code = d.get("origin_country", "")
            try:
                country_name = pycountry.countries.get(
                    alpha_2=code).name if code else "Unknown"
            except:
                country_name = "Unknown"
            countries.append(country_name)
        return countries
    return []


df["production_company_countries"] = df["production_companies"].apply(
    get_country_names)

df["production_company_names_str"] = df["production_company_names"].apply(
    lambda x: ", ".join(x) if x else "Unknown"
)

df["production_company_countries_str"] = df["production_company_countries"].apply(
    lambda x: ", ".join(x) if x else "Unknown"
)

print(df[["production_company_names_str",
      "production_company_countries_str"]].head(10))

C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\4232442197.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["production_companies"] = df["production_companies"].apply(
C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\4232442197.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["production_company_names"] = df["production_companies"].apply(
C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\4232442197.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try u

  production_company_names_str production_company_countries_str
0                      Unknown                          Unknown
1                     Hepworth                   United Kingdom
2                      Unknown                          Unknown
3               Edison Studios                    United States
4               Edison Studios                    United States
5               Edison Studios                    United States
6                      Unknown                          Unknown
7               Edison Studios                    United States
8               Edison Studios                    United States
9                      Unknown                          Unknown


C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\4232442197.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["production_company_countries_str"] = df["production_company_countries"].apply(


In [14]:
df["release_date"] = pd.to_datetime(df["release_date"], errors="coerce")
df["release_year"] = df["release_date"].dt.year
df["release_month"] = df["release_date"].dt.month
df["release_day"] = df["release_date"].dt.day

C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\2610998959.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["release_date"] = pd.to_datetime(df["release_date"], errors="coerce")
C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\2610998959.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["release_year"] = df["release_date"].dt.year
C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\2610998959.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[

In [17]:
df.isnull().sum()

adult                               0
budget                              0
id                                  0
origin_country                      0
original_language                   0
overview                            0
popularity                          0
production_companies                0
production_countries                0
release_date                        0
revenue                             0
runtime                             0
title                               4
vote_average                        0
vote_count                          0
genre_names                         0
genre_names_str                     0
genre_names_list                    0
production_company_names            0
production_company_countries        0
production_company_names_str        0
production_company_countries_str    0
release_year                        0
release_month                       0
release_day                         0
dtype: int64

In [11]:
df


adult      budget       id origin_country original_language  \
0       False     1674.45   195554         ['US']                en   
1       False   889944.00   105303         ['GB']                xx   
2       False     3778.70   195553         ['US']                en   
3       False   199551.00   195569         ['US']                en   
4       False   241279.00   195542         ['US']                en   
...       ...         ...      ...            ...               ...   
946894  False   176436.50  1554419         ['US']                en   
946895  False      300.00  1554303         ['IT']                it   
946896  False    17000.00  1554304         ['IN']                ta   
946897  False  1309940.00  1355140         ['ID']                id   
946898  False      402.00  1554299         ['DO']                es   

                                                 overview  popularity  \
0       This building and machinery supplied the elect...      6.3707   
1       An early trick film where a car explodes and b...      3.4255   
2       This is the building in which so many of the p...      3.2375   
3       This picture shows the remains of one of the d...      5.1725   
4       At the first news of the disast by cyclone and...      4.0098   
...                                                   ...         ...   
946894  After Paola is matched with a handsome online ...      0.0000   
946895                              No overview available      0.0000   
946896  Francis' father raises his voice for an import...      0.0000   
946897  Sabdo and Intan lived happily despite their ma...      0.9564   
946898                              No overview available      0.0000   

                                     production_companies  \
0                                                      []   
1       [{'id': 24148, 'logo_path': None, 'name': 'Hep...   
2                                                      []   
3       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
4       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
...                                                   ...   
946894                                                 []   
946895  [{'id': 275779, 'logo_path': None, 'name': 'Fa...   
946896                                                 []   
946897  [{'id': 5344, 'logo_path': '/QDZf41MZk122e61pZ...   
946898  [{'id': 168180, 'logo_path': None, 'name': 'Ca...   

                                     production_countries release_date  ...  \
0                                                      []   1900-05-21  ...   
1        [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   1900-07-01  ...   
2                                                      []   1900-09-21  ...   
3       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21  ...   
4       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21  ...   
...                                                   ...          ...  ...   
946894                                                 []          NaT  ...   
946895            [{'iso_3166_1': 'IT', 'name': 'Italy'}]   2025-10-21  ...   
946896                                                 []   2025-12-19  ...   
946897        [{'iso_3166_1': 'ID', 'name': 'Indonesia'}]   2025-12-24  ...   
946898  [{'iso_3166_1': 'DO', 'name': 'Dominican Repub...   2025-12-04  ...   

        production_company_names  production_company_countries  \
0                             []                            []   
1                     [Hepworth]              [United Kingdom]   
2                             []                            []   
3               [Edison Studios]               [United States]   
4               [Edison Studios]               [United States]   
...                          ...                           ...   
946894                        []                            []   
946895      [Fast Brains Studio]                     [Unknown]   
94

In [21]:
import pandas as pd
import numpy as np
import random

# مثال: الداتا بتاعتك
# df = pd.read_csv('movies.csv')

# خريطة الرنجات لكل نوع ولكل عقد
budget_ranges = {
    'Documentary': {1960: (5e3, 1e5), 2000: (5e4, 5e5), 2020: (1e5, 2e6)},
    'Comedy': {1960: (5e4, 5e5), 2000: (5e5, 5e6), 2020: (1e6, 3e7)},
    'Action': {1960: (1e5, 1e6), 2000: (5e6, 3e7), 2020: (1e7, 2e8)},
    'Animation': {1960: (5e4, 5e5), 2000: (5e6, 2e7), 2020: (1e7, 1.5e8)},
}

revenue_ranges = {
    'Documentary': {1960: (1e4, 5e5), 2000: (5e4, 2e6), 2020: (2e5, 5e6)},
    'Comedy': {1960: (1e5, 5e6), 2000: (5e5, 5e7), 2020: (1e6, 1e8)},
    'Action': {1960: (5e5, 1e7), 2000: (5e6, 5e8), 2020: (5e6, 1e9)},
    'Animation': {1960: (2e5, 2e6), 2000: (1e6, 1e8), 2020: (5e6, 8e8)},
}

def get_decade(year):
    if pd.isna(year):
        return 2020
    return int(year) - int(year) % 10

def get_random_value(genres, year, ranges_dict):
    decade = get_decade(year)
    vals = []
    for g in genres:
        g = g.strip()
        if g in ranges_dict:
            # لو العقد مش موجود ناخد أقرب عقد متاح
            if decade not in ranges_dict[g]:
                decade_key = max([d for d in ranges_dict[g].keys() if d <= decade], default=2020)
            else:
                decade_key = decade
            low, high = ranges_dict[g][decade_key]
            vals.append(random.uniform(low, high))
    if not vals:
        return np.nan
    return np.mean(vals)  # ناخد المتوسط بين الأنواع المختلفة

# نفترض إن genre_names_list فيها ليست للأنواع
# لو مش عندك العمود ده، ممكن تعمل:
# df['genre_names_list'] = df['genre_names_str'].apply(lambda x: [g.strip() for g in x.split(',')] if pd.notna(x) else [])

# تعبئة القيم المفقودة في budget
df['budget'] = df.apply(
    lambda row: row['budget'] if pd.notna(row['budget']) and row['budget'] > 0 
    else get_random_value(row['genre_names_list'], row['release_year'], budget_ranges),
    axis=1
)

# تعبئة القيم المفقودة في revenue
df['revenue'] = df.apply(
    lambda row: row['revenue'] if pd.notna(row['revenue']) and row['revenue'] > 0 
    else get_random_value(row['genre_names_list'], row['release_year'], revenue_ranges),
    axis=1
)


C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\3333557353.py:50: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['budget'] = df.apply(
C:\Users\ASUS\AppData\Local\Temp\ipykernel_648\3333557353.py:57: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['revenue'] = df.apply(


In [23]:
df

adult        budget       id origin_country original_language  \
0       False  3.210640e+07   195554         ['US']                en   
1       False  2.038359e+07   105303         ['GB']                xx   
2       False  4.743289e+07   195553         ['US']                en   
3       False  2.861975e+05   195569         ['US']                en   
4       False  1.077016e+06   195542         ['US']                en   
...       ...           ...      ...            ...               ...   
946891  False           NaN  1554339         ['US']                en   
946895  False  3.000000e+02  1554303         ['IT']                it   
946896  False  1.700000e+04  1554304         ['IN']                ta   
946897  False           NaN  1355140         ['ID']                id   
946898  False  1.255883e+07  1554299         ['DO']                es   

                                                 overview  popularity  \
0       This building and machinery supplied the elect...      6.3707   
1       An early trick film where a car explodes and b...      3.4255   
2       This is the building in which so many of the p...      3.2375   
3       This picture shows the remains of one of the d...      5.1725   
4       At the first news of the disast by cyclone and...      4.0098   
...                                                   ...         ...   
946891  A young man grappling with melancholy is stunn...      0.0000   
946895                              No overview available      0.0000   
946896  Francis' father raises his voice for an import...      0.0000   
946897  Sabdo and Intan lived happily despite their ma...      0.9564   
946898                              No overview available      0.0000   

                                     production_companies  \
0                                                      []   
1       [{'id': 24148, 'logo_path': None, 'name': 'Hep...   
2                                                      []   
3       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
4       [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
...                                                   ...   
946891                                                 []   
946895  [{'id': 275779, 'logo_path': None, 'name': 'Fa...   
946896                                                 []   
946897  [{'id': 5344, 'logo_path': '/QDZf41MZk122e61pZ...   
946898  [{'id': 168180, 'logo_path': None, 'name': 'Ca...   

                                     production_countries release_date  ...  \
0                                                      []   1900-05-21  ...   
1        [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   1900-07-01  ...   
2                                                      []   1900-09-21  ...   
3       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21  ...   
4       [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21  ...   
...                                                   ...          ...  ...   
946891   [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   2025-10-08  ...   
946895            [{'iso_3166_1': 'IT', 'name': 'Italy'}]   2025-10-21  ...   
946896                                                 []   2025-12-19  ...   
946897        [{'iso_3166_1': 'ID', 'name': 'Indonesia'}]   2025-12-24  ...   
946898  [{'iso_3166_1': 'DO', 'name': 'Dominican Repub...   2025-12-04  ...   

                    genre_names        genre_names_str  \
0                            []              Animation   
1                      [Comedy]                 Comedy   
2                            []              Animation   
3                 [Documentary]            Documentary   
4                 [Documentary]            Documentary   
...                         ...                    ...   
946891                  [Drama]                  Drama   
946895         [Action, Comedy]         Action, Comedy   
946896                 [Action]                 Ac

In [22]:
df.columns

Index(['adult', 'budget', 'id', 'origin_country', 'original_language',
       'overview', 'popularity', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime', 'title',
       'vote_average', 'vote_count', 'genre_names', 'genre_names_str',
       'genre_names_list', 'production_company_names',
       'production_company_countries', 'production_company_names_str',
       'production_company_countries_str', 'release_year', 'release_month',
       'release_day'],
      dtype='object')

In [20]:
print(df.genre_names_str.unique())

['Animation' 'Comedy' 'Documentary' ... 'Horror, Comedy, Drama, Action'
 'History, War, Drama, Crime' 'Comedy, Horror, Animation, Fantasy']


In [ ]:
df['budget'].unique().sum()

np.float64(nan)

In [5]:
df["budget"] = df["budget"].replace(0, pd.NA)
df["revenue"] = df["revenue"].replace(0, pd.NA)

In [47]:
df["profit"] = df["revenue"] - df["budget"]

In [48]:
# Calculate ROI and handle division by zero (when budget is 0) RoI( Return on Investment )
df["roi"] = (df["profit"] / df["budget"]).round(2)

In [49]:
df["adult"] = df["adult"].astype(int)  # 0 = False, 1 = True

In [50]:
df["overview_length"] = df["overview"].apply(lambda x: len(str(x).split()))

In [51]:
df.head(10)

adult  budget      id origin_country original_language  \
0      0       0  195554         ['US']                en   
1      0       0  105303         ['GB']                xx   
2      0       0  195553         ['US']                en   
3      0       0  195569         ['US']                en   
4      0       0  195542         ['US']                en   
5      0       0  195631         ['US']                en   
6      0       0  811141         ['GB']                en   
7      0       0  195668         ['US']                en   
8      0       0  144432         ['US']                en   
9      0       0  536198         ['FR']                fr   

                                            overview  popularity  \
0  This building and machinery supplied the elect...      6.3707   
1  An early trick film where a car explodes and b...      3.4255   
2  This is the building in which so many of the p...      3.2375   
3  This picture shows the remains of one of the d...      5.1725   
4  At the first news of the disast by cyclone and...      4.0098   
5  This is a new adventure in which our friend, M...      3.1284   
6  A Victorian vaudeville routine is given the bi...      2.9259   
7  As the above title indicates, the scene does n...      2.7771   
8  A cartoonist defies reality when he draws obje...      2.7038   
9               An adaptation of the biblical story.      2.4877   

                                production_companies  \
0                                                 []   
1  [{'id': 24148, 'logo_path': None, 'name': 'Hep...   
2                                                 []   
3  [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
4  [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
5  [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
6                                                 []   
7  [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
8  [{'id': 18758, 'logo_path': '/fe3cMUJLhbkTM9PD...   
9                                                 []   

                                production_countries release_date  ...  \
0                                                 []   1900-05-21  ...   
1   [{'iso_3166_1': 'GB', 'name': 'United Kingdom'}]   1900-07-01  ...   
2                                                 []   1900-09-21  ...   
3  [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21  ...   
4  [{'iso_3166_1': 'US', 'name': 'United States o...   1900-09-21  ...   
5  [{'iso_3166_1': 'US', 'name': 'United States o...   1900-11-01  ...   
6                                                 []   1900-01-01  ...   
7  [{'iso_3166_1': 'US', 'name': 'United States o...   1901-12-16  ...   
8  [{'iso_3166_1': 'US', 'name': 'United States o...   1900-11-16  ...   
9           [{'iso_3166_1': 'FR', 'name': 'France'}]   1901-05-28  ...   

   production_company_names  production_company_countries  \
0                        []                            []   
1                [Hepworth]              [United Kingdom]   
2                        []                            []   
3          [Edison Studios]               [United States]   
4          [Edison Studios]               [United States]   
5          [Edison Studios]               [United States]   
6                        []                            []   
7          [Edison Studios]               [United States]   
8          [Edison Studios]               [United States]   
9                        []                            []   

  production_company_names_str  production_company_countries_str  \
0                      Unknown                           Unknown   
1                     Hepworth                    United Kingdom   
2                      Unknown                           Unknown   
3               Edison Studios                     United States   
4               Edison Studios                     United States   
5               Edison Studios                     United States   
6 

In [36]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 946899 entries, 0 to 946898
Data columns (total 21 columns):
 #   Column                        Non-Null Count   Dtype         
---  ------                        --------------   -----         
 0   id                            946899 non-null  int64         
 1   title                         946895 non-null  object        
 2   original_language             946899 non-null  object        
 3   origin_country                946899 non-null  object        
 4   genre_names                   946899 non-null  object        
 5   production_company_names      946899 non-null  object        
 6   release_date                  946464 non-null  datetime64[ns]
 7   runtime                       946899 non-null  float64       
 8   budget                        58706 non-null   object        
 9   revenue                       23588 non-null   object        
 10  popularity                    946899 non-null  float64       
 11  vote_average 

In [52]:
df["original_language"] = df["original_language"].replace({
    "xx": "unknown",
    "cn": "zh"
})

In [53]:

def get_language_name(code):
    try:
        return pycountry.languages.get(alpha_2=code).name
    except:
        return "Unknown"


df["original_language_name"] = df["original_language"].apply(get_language_name)

In [54]:
lang_counts = df["original_language"].value_counts().head(10)
print(lang_counts)

original_language
en    445905
fr     60939
es     58765
de     46032
ja     43812
zh     32663
pt     30701
ru     25046
it     22760
ko     12760
Name: count, dtype: int64


In [55]:
# خليك متأكد إن الأعمدة الأساسية بترتب الأول
main_cols = [
    "id", "title", "original_language", "origin_country",
    "genre_names", "production_companies", "release_date",
    "runtime", "budget", "revenue", "popularity", "vote_average",
    "vote_count", "overview", "adult"
]

# أي أعمدة زيادة (هتتحط بعد الأساسية)
other_cols = [col for col in df.columns if col not in main_cols]

df = df[main_cols + other_cols]

In [56]:
df['original_language'].unique()

array(['en', 'unknown', 'fr', 'es', 'fa', 'nl', 'it', 'ja', 'da', 'sv',
       'cs', 'de', 'hu', 'pl', 'zh', 'mk', 'sl', 'pt', 'sr', 'hr', 'no',
       'ru', 'fi', 'ar', 'is', 'ka', 'uk', 'sh', 'yi', 'el', 'la', 'et',
       'ca', 'mr', 'he', 'tl', 'ro', 'lv', 'bg', 'gu', 'mi', 'tr', 'af',
       'az', 'ab', 'ta', 'hi', 'ko', 'bn', 'sk', 'jv', 'my', 'th', 'uz',
       'hy', 'vi', 'be', 'cv', 'gl', 'id', 'ml', 'lt', 'ay', 'te', 'ur',
       'ga', 'kn', 'cy', 'ms', 'mn', 'or', 'fy', 'as', 'kk', 'sq', 'nb',
       'si', 'ps', 'dz', 'mo', 'lb', 'nn', 'ne', 'pa', 'ty', 'tg', 'sd',
       'ky', 'eu', 'km', 'qu', 'lo', 'wo', 'ug', 'am', 'sa', 'tk', 'ks',
       'ln', 'eo', 'ha', 'st', 'so', 'fj', 'ku', 'mt', 'zu', 'kl', 'cr',
       'br', 'xh', 'iu', 'bm', 'mg', 'sw', 'se', 'ht', 'yo', 'fo', 'av',
       'ff', 'gd', 'co', 'bi', 'oc', 'rm', 'ee', 'ig', 'bs', 'bo', 'an',
       'tn', 'tt', 'sm', 'rw', 'dv', 'kw', 'ba', 'ti', 'kj', 'gn', 'ce',
       'kv', 'sn', 'ak', 'to', 'ik', 'tw', 'ts', 'nv

In [57]:
df.isnull().sum()

id                                       0
title                                    4
original_language                        0
origin_country                           0
genre_names                              0
production_companies                     0
release_date                           435
runtime                                  0
budget                                   0
revenue                                  0
popularity                               0
vote_average                             0
vote_count                               0
overview                                 0
adult                                    0
production_countries                     0
genre_names_str                          0
production_company_names                 0
production_company_countries             0
production_company_names_str             0
production_company_countries_str         0
release_year                           435
release_month                          435
release_day

In [17]:
df.to_csv(r"D:\depi_project\data\processed\movies_all_cleaned.csv", index=False)

In [ ]:
/*****************************
1)  BULK INSERT staging (CSV files)
*****************************/
-- staging_movies (main)
IF OBJECT_ID('dbo.staging_movies','U') IS NULL
BEGIN
  CREATE TABLE dbo.staging_movies (
    id INT,
    title NVARCHAR(1000),
    adult BIT,
    original_language NVARCHAR(10),
    origin_country NVARCHAR(200),
    release_date DATE,
    release_year INT,
    release_month INT,
    release_day INT,
    overview NVARCHAR(MAX),
    genre_names_str NVARCHAR(MAX),
    production_company_names_str NVARCHAR(MAX),
    production_company_countries_str NVARCHAR(MAX),
    budget NVARCHAR(100),
    revenue NVARCHAR(100),
    runtime INT,
    popularity FLOAT,
    vote_average FLOAT,
    vote_count INT,
    roi_calculated FLOAT
  );
END
GO


BULK INSERT dbo.staging_movies
FROM 'C:\data\movies_clean.csv'
WITH (
  FIRSTROW = 2,
  FIELDTERMINATOR = ',',
  ROWTERMINATOR = '\n',
  CODEPAGE = '65001',  -- utf-8
  TABLOCK
);
GO